In [21]:
import datajoint as dj
import numpy as np

dj.config["database.host"] = "10.28.0.34"
dj.config["database.user"] = "celiib"
dj.config["database.password"] = "newceliipass"
dj.config["safemode"] = True
dj.config["display.limit"] = 20

pinky = dj.create_virtual_module("pinky","microns_pinky")
schema = dj.schema("microns_pinky")

In [ ]:
#get the indices of the component
component_mesh_key = dict(compartment_type="Apical",segmentation=3,
                       segment_id=648518346349509855,
                       component_index=0,
                        decimation_ratio= 0.35
                       )

In [ ]:
verts_labels,triangles_labels = (pinky.ComponentLabelFinal & component_mesh_key).fetch1("labeled_vertices","labeled_triangles")
verts_labels = verts_labels.astype("int") 
triangles_labels = triangles_labels.astype("int") 
#where to insert the new code
verts_labels[verts_labels == 0] = 17
triangles_labels[triangles_labels == 0] = 17

In [ ]:
pinky.ProofreadLabelSpineWithInterest()

In [ ]:
current_done_table = dj.U("segment_id","compartment_type","component_index") & pinky.ProofreadLabelSpine

In [ ]:
pinky.ProofreadLabelSpineWithInterest

In [ ]:
@schema
class ProofreadLabelSpineWithInterest(dj.Manual):
    definition="""
    -> pinky.CompartmentFinal.ComponentFinal
    author_original      : varchar(20)                  # name of last editor
    author_proofreader   : varchar(20)                  # name of last editor
    date_time=CURRENT_TIMESTAMP : timestamp                    # the last time it was edited
    ---
    vertices             : longblob                     # label data for the vertices
    triangles            : longblob                     # label data for the faces
    edges                : longblob                     # label data for the edges
    status               : varchar(16)                  # the index of the status descriptor that can be references by the StatusKey
    interest_description : varchar(1000)                # short description about why this dendrite is interesting
    """


In [ ]:
pinky.ProofreadLabelSpineWithInterest()

In [ ]:
proofread_segments = pinky.ProofreadLabelSpine.fetch("segment_id",order_by="date_time")
proofread_segments

In [ ]:
segment_ids = pinky.SpineValidationCompartmentFinalComponentFinal.fetch(order_by="process_order",as_dict=True)
segment_ids[:18]

In [ ]:
pinky.ProofreadLabelSpine() & "status!='complete'"

# Creating table that does slices

In [ ]:
pinky.Segment.describe()

In [ ]:
pinky.CompartmentFinal.ComponentFinal()
key = dict(segment_id=648518346341371119,compartment_type="Apical",component_index=0)
n_triangles = (pinky.CompartmentFinal.ComponentFinal & key).fetch1("n_triangle_indices")
n_triangles

In [ ]:
import random
@schema
class ProofreadLabelSpineRandomStart(dj.Computed):
    definition="""
    -> pinky.SpineValidationCompartmentFinalComponentFinal
    ---
    starting_index       : int unsigned                 # automatically generated starting index for the slice generation algorithm
    """
    key_source = pinky.SpineValidationCompartmentFinalComponentFinal()
    
    def make(self,key):
        print("Working on " + str(key))
        #get the number of triangles in the component
        n_triangles = (pinky.CompartmentFinal.ComponentFinal & key).fetch1("n_triangle_indices")
        
        #get a random number
        starting_index = random.randint(0,n_triangles)
        
        #insert into table
        self.insert1(dict(key,starting_index=starting_index))
        

In [ ]:
#ProofreadLabelSpineRandomStart.drop()

In [ ]:
ProofreadLabelSpineRandomStart.populate()

In [ ]:
ProofreadLabelSpineRandomStart()

In [11]:
component_mesh_key = {'segment_id': 648518346349513079, 'decimation_ratio': 0.35, 'compartment_type': 'Oblique', 'component_index': 2, 'segmentation': 3}

In [14]:
pinky.ProofreadLabelSpineRandomStart() & component_mesh_key

*process_order *segmentation  *segment_id    *decimation_ra *compartment_t *component_ind starting_index
+------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+
17             3              64851834634951 0.35           Oblique        2              46546         
245            3              64851834634951 0.35           Oblique        2              17958         
 (Total: 2)

In [13]:
starting_index_db = (pinky.ProofreadLabelSpineRandomStart & component_mesh_key).fetch("starting_index",order_by="process_order")[0]
starting_index_db

46546

In [18]:
ProofreadLabelSpineWithInterestSlices()

*segmentation  *segment_id    *decimation_ra *compartment_t *component_ind *author_origin *author_proofr *starting_inde *n_triangles   *date_time    n_vertices     vertices   triangles  triangle_i edges      status     interest_descr
+------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +-----------+ +------------+ +--------+ +--------+ +--------+ +--------+ +--------+ +------------+

 (Total: 0)

In [15]:
#ProofreadLabelSpineWithInterestSlices.drop()

`microns_pinky`.`proofread_label_spine_with_interest_slices` (1 tuples)


Proceed? [yes, No]:  yes


Tables dropped.  Restart kernel.


In [17]:
@schema
class ProofreadLabelSpineWithInterestSlices(dj.Manual):
    definition="""
    -> pinky.CompartmentFinal.ComponentFinal
    author_original      : varchar(20)                  # name of last editor
    author_proofreader   : varchar(20)                  # name of last editor
    starting_index       : int unsigned                 # starting index for the slice generation algorithm
    n_triangles          : int unsigned                 # number of triangles used for slice
    date_time=CURRENT_TIMESTAMP : timestamp             # the last time it was edited
    ---
    n_vertices           : int unsigned                 # number of vertices as a result of the slice size of n_triangles
    vertices             : longblob                     # label data for the vertices
    triangles            : longblob                     # label data for the faces
    triangle_indices     : longblob                     # the indicies of the triangles used in the slice of the dendrite 
    edges                : longblob                     # label data for the edges
    status               : varchar(16)                  # the index of the status descriptor that can be references by the StatusKey
    interest_description : varchar(1000)                # short description about why this dendrite is interesting
    """


In [ ]:
"""
Brainstorming the changes to make to labeler for adding slices
- Have a default slice size (and have it displayed in a text box)

- When loading the neuron
a. Download the starting index
b. Retrieve the slice size (DON'T NEED to store it as attribute)
1) Have to change the dummy partial write at the beginning
b. Pull from the slice size to input for n_triangles and triangle_indices
2) When creating the mesh
a. Send the vertices,faces,slice_size and starting index to the function that extracts submesh
b. Use these new vertices and slices for the mesh
c ***** need to change the function to return and save the indices of the submesh somewhere so can write it to the database when done ******

- when writing the neuron:
a. Don't pull from the slice size to determine size of the neuron slice (because the text field could have been editied since that point)
 > instead just use the size of the mesh object
b. Pull down the starting_index and triangle indices from the partial or complete one so can restore them


- Panel:
Just text edit box that can be used to input the size of the slice

*** will now have to append the slice size to all of the names ***



How the process of slice size is going to work:
1) 


"""



In [1]:
import numpy as np

In [4]:
np.linspace(0,10,11).astype("int")

array([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10])

# Checking that the indices stored match the ones we are editing

In [38]:
component_mesh_key = dict(compartment_type="Apical",segmentation=3,
                       segment_id=int(648518346349499297),
                       component_index=int(0),
                        decimation_ratio= 0.35
                       )
    

triangle_indices_random = (pinky.ProofreadLabelSpineWithInterestSlices() & component_mesh_key).fetch1("triangle_indices")

In [27]:
pinky.CompartmentFinal.ComponentFinal()

*segmentation  *segment_id    *decimation_ra *compartment_t *component_ind n_vertex_indic n_triangle_ind vertex_ind triangle_i
+------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +--------+ +--------+
3              64851834634137 0.35           Apical         0              115133         230349         =BLOB=     =BLOB=    
3              64851834634137 0.35           Axon-Soma      0              1567           3108           =BLOB=     =BLOB=    
3              64851834634137 0.35           Basal          0              4231           8416           =BLOB=     =BLOB=    
3              64851834634137 0.35           Basal          1              110            208            =BLOB=     =BLOB=    
3              64851834634137 0.35           Basal          2              22310          44613          =BLOB=     =BLOB=    
3              64851834634137 0.35           Basal          3              1021           1988           =BLOB=     =BLOB=    
3              64851834634137 0.35           Basal          4              40075          80121          =BLOB=     =BLOB=    
3              64851834634137 0.35           Basal          5              514            954            =BLOB=     =BLOB=    
3              64851834634137 0.35           Cilia          0              111            216            =BLOB=     =BLOB=    
3              64851834634137 0.35           Error          0              716            1423           =BLOB=     =BLOB=    
3              64851834634137 0.35           Oblique        0              10066          20142          =BLOB=     =BLOB=    
3              64851834634137 0.35           Soma           0              27356          54399          =BLOB=     =BLOB=    
3              64851834634938 0.35           Axon-Soma      0              817            1600           =BLOB=     =BLOB=    
3              64851834634938 0.35           Basal          0              2              0              =BLOB=     =BLOB=    
3              64851834634938 0.35           Basal          1              15855          31692          =BLOB=     =BLOB=    
3              64851834634938 0.35           Soma           0              11324          22632          =BLOB=     =BLOB=    
3              64851834634947 0.35           Apical         0              10652          21204          =BLOB=     =BLOB=    
3              64851834634947 0.35           Axon-Soma      0              53876          107708         =BLOB=     =BLOB=    
3              64851834634947 0.35           Basal          0              9356           18676          =BLOB=     =BLOB=    
3              64851834634947 0.35           Basal          1              12166          24340          =BLOB=     =BLOB=    
   ...
 (Total: 3859)

In [34]:
#get the full mesh and then the component
verts,faces = (pinky.PymeshfixDecimatedExcitatoryStitchedMesh & component_mesh_key).fetch1("vertices","triangles")
#get the indices for the compartment component
triangle_indices = (pinky.CompartmentFinal.ComponentFinal & component_mesh_key).fetch("triangle_indices")

In [35]:
verts

array([[451574.375     , 241430.125     ,  11299.79296875],
       [336728.65625   , 210543.859375  ,  72062.125     ],
       [451294.375     , 241271.484375  ,  11398.79492188],
       ...,
       [451559.75      , 228481.        ,  33580.38671875],
       [451454.03125   , 228521.828125  ,  33625.5390625 ],
       [451618.90625   , 228376.9375    ,  33507.4453125 ]])

In [37]:
#get the submesh of the compartment component
import trimesh
whole_mesh = trimesh.Trimesh(verts,faces,process=False)
whole_mesh.show()
comp_mesh = whole_mesh.submesh(triangle_indices,append=True)
comp_mesh.show()

c:\users\celii\appdata\local\programs\python\python35\lib\site-packages\IPython\core\display.py:694: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [40]:
#how see if the triangle indices saved are the ones that match the randomly stored mesh
random_mesh = comp_mesh.submesh([triangle_indices_random],append=True)
random_mesh.show()

c:\users\celii\appdata\local\programs\python\python35\lib\site-packages\IPython\core\display.py:694: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [43]:
# test to see if the labels saved correspond in the right way
spine_labels = (pinky.ProofreadLabelSpineWithInterestSlices() & component_mesh_key).fetch1("triangles")
spine_labels

array([17, 17, 17, ..., 17, 17, 17], dtype=uint8)

In [49]:
spines = random_mesh.submesh(np.where(spine_labels != 17),append=True)
spines.show()

c:\users\celii\appdata\local\programs\python\python35\lib\site-packages\IPython\core\display.py:694: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [ ]:
"""
Conclusion: 
Everything is working perfectly fine with saving the labels and the vertices

"""

In [50]:
pinky.ProofreadLabelSpineWithInterest()

*segmentation  *segment_id    *decimation_ra *compartment_t *component_ind *author_origin *author_proofr *date_time     vertices   triangles  edges      status       interest_descr
+------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +--------+ +--------+ +--------+ +----------+ +------------+
3              64851834634949 0.35           Basal          2              computer_Auto  js48           2019-08-01 16: =BLOB=     =BLOB=     =BLOB=     partial                    
3              64851834634949 0.35           Oblique        1              computer_Auto  js48           2019-08-01 18: =BLOB=     =BLOB=     =BLOB=     complete                   
3              64851834634949 0.35           Apical         0              computer_Auto  js48           2019-08-01 14: =BLOB=     =BLOB=     =BLOB=     complete                   
3              64851834634950 0.35           Oblique        3              computer_Auto  js48           2019-08-01 15: =BLOB=     =BLOB=     =BLOB=     complete                   
3              64851834634950 0.35           Basal          0              computer_Auto  js48           2019-08-01 13: =BLOB=     =BLOB=     =BLOB=     complete                   
3              64851834634950 0.35           Basal          4              computer_Auto  js48           2019-08-01 18: =BLOB=     =BLOB=     =BLOB=     partial                    
3              64851834634950 0.35           Apical         0              computer_Auto  js48           2019-08-01 17: =BLOB=     =BLOB=     =BLOB=     complete                   
3              64851834634951 0.35           Oblique        2              computer_Auto  spapadop       2019-08-01 11: =BLOB=     =BLOB=     =BLOB=     partial                    
 (Total: 8)

In [58]:
pinky.ProofreadLabelSpineWithInterestSlices()#.delete()

*segmentation  *segment_id    *decimation_ra *compartment_t *component_ind *author_origin *author_proofr *starting_inde *n_triangles   *date_time    n_vertices     vertices   triangles  triangle_i edges      status     interest_descr
+------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +-----------+ +------------+ +--------+ +--------+ +--------+ +--------+ +--------+ +------------+

 (Total: 0)

In [55]:
component_mesh_key = {'component_index': 0, 'segmentation': 3, 'segment_id': 648518346349500049, 'decimation_ratio': 0.35, 'compartment_type': 'Apical'}
pinky.CompartmentFinal.ComponentFinal() & component_mesh_key

*segmentation  *segment_id    *decimation_ra *compartment_t *component_ind n_vertex_indic n_triangle_ind vertex_ind triangle_i
+------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +------------+ +--------+ +--------+
3              64851834634950 0.35           Apical         0              14536          28999          =BLOB=     =BLOB=    
 (Total: 1)

# Doing the orphan branches

In [ ]:
@schema
class ProofreadLabelSpineWithInterestSlicesOrphan(dj.Manual):
    definition="""
    -> pinky.CompartmentOrphan.ComponentOrphan
    author_original      : varchar(20)                  # name of last editor
    author_proofreader   : varchar(20)                  # name of last editor
    starting_index       : int unsigned                 # starting index for the slice generation algorithm
    n_triangles          : int unsigned                 # number of triangles used for slice
    date_time=CURRENT_TIMESTAMP : timestamp             # the last time it was edited
    ---
    n_vertices           : int unsigned                 # number of vertices as a result of the slice size of n_triangles
    vertices             : longblob                     # label data for the vertices
    triangles            : longblob                     # label data for the faces
    triangle_indices     : longblob                     # the indicies of the triangles used in the slice of the dendrite 
    edges                : longblob                     # label data for the edges
    status               : varchar(16)                  # the index of the status descriptor that can be references by the StatusKey
    interest_description : varchar(1000)                # short description about why this dendrite is interesting
    """
